# Sorting a playlist in a simple way


In [1]:
from pathlib import Path
import librosa, librosa.display
import numpy as np, scipy, matplotlib.pyplot as plt, sklearn, librosa, mir_eval, IPython.display, urllib
from mpl_toolkits.mplot3d import Axes3D

In [2]:
tempos = []
for p in Path().glob('songset/*.mp3'):
    y, sr = librosa.load(p, offset=30.0, duration=10.0)
    onset_env = librosa.onset.onset_strength(y, sr=sr)
    tempo = librosa.beat.tempo(onset_envelope=onset_env, sr=sr)
    tempos.append((y, sr, round(tempo[0])))
    print(round(tempo[0]))

117.0
112.0
123.0
123.0
117.0


# Organize
this will be the simplest form of organization <br/>
**all** I want to do is create a wave of tempos starting slow then increasing 

In [12]:
count = 0
increament = round(len(tempos) / 3)
current = 0
sorted(tempos, key=lambda song: song[2])
relativeOrder = []
while count != len(tempos):
    print(current)
    relativeOrder.append(tempos[current])
    current = (current + increament) % len(tempos)
    count += 1
    


0
2
4
1
3


# Displaying the audio files 
I have simplay concatinated the songs together to make listening to them more fluent

In [29]:
combinedSongs = []
for song in relativeOrder:
    for val in song[0]:
        combinedSongs.append(val)
IPython.display.Audio(combinedSongs, rate=tempos[0][1])

# Now I will make use of Clustering
I run into a couple of problems when I think about using clustering. 

The first problem comes when I have to transition from one cluster to another, how do I know which cluster to transition too???


# Using MFCC 


In [17]:
mfccs = []
for song in tempos:
    mfcc = librosa.feature.mfcc(song[0], sr=song[1])
    mfccs.append(mfcc.flatten())
    
scaler = sklearn.preprocessing.StandardScaler()
scaler.fit(mfccs)
features_scaled = scaler.transform(mfccs)
print(features_scaled.shape)

(5, 8620)


# Clustering the above normalized data


In [18]:
model = sklearn.cluster.AffinityPropagation()
labels = model.fit_predict(features_scaled)
print(labels)

[1 0 1 1 1]


# Sorting the songs wrt their Label
* here we sort each of the clusters by tempo in non-decreasing order 
* then in a way we have discused I play the song from slow to fast withing the cluster 

In [33]:
groupedSongs = {}
for i in range(len(labels)):
    if labels[i] in groupedSongs:
        groupedSongs[labels[i]].append(tempos[i])
    else:
        grouped = [tempos[i]]
        groupedSongs[labels[i]] = grouped

clusteredOrder = []

for key,val in groupedSongs.items():
    count = 0
    increament = int(len(tempos) / 3)
    current = 0
    sorted(val, key=lambda song: song[2])
    while count != len(val):
        print(current)
        clusteredOrder.append(val[current])
        current = (current + increament) % len(val)
        count += 1
        

0
1
2
3
0


# Playing the songs grouped by cluster
* again we are using the start slow and then go fast approach 
* we have **not** performed the most efficient cluster transition though

In [32]:
combinedSongs = []
for song in clusteredOrder:
    for val in song[0]:
        combinedSongs.append(val)
IPython.display.Audio(combinedSongs, rate=tempos[0][1])